### Code to create Mini-Reddit

In [1]:
from pathlib import Path
from garage.data import image_listing
from PIL import Image
from random import shuffle
import shutil
from tqdm import tqdm
import re

import numpy as np
import math

In [2]:
reddit_dir = Path("~/me/data/reddit").expanduser()
assert reddit_dir.exists()
subreddit_dir = [d for d in reddit_dir.iterdir() if d.is_dir()]
image_files = image_listing.find_images(reddit_dir)
print(len(image_files))

179443


In [3]:
output_dir =  Path("~/me/data/reddit-tiny").expanduser()
pcnt = 0.05
num_image_files = len(image_files)
num_out_files = int(math.ceil(pcnt*num_image_files))
shuffle(image_files)
num_out_files
output_dir.mkdir()

In [4]:
num_out_files

8973

In [5]:
idx = 0
with tqdm(total=num_out_files) as pbar:
    
    while idx < num_image_files:
        f = Path(image_files[idx])
        idx = idx + 1

        try:
            im = Image.open(f)
            size = im.size
            pixels = max(1, size[0]) * max(1, size[1])

            if pixels > Image.MAX_IMAGE_PIXELS: continue
            nim = np.array(im)
            if len(nim.shape)!= 3 or nim.shape[-1] != 3 : continue

            subreddit = f.relative_to(reddit_dir).parent
       
            dname = subreddit.name           
            dname = dname.lower()
            if "porn" in dname:
                dname = dname.replace("porn", "")

            subreddit_dir = output_dir / subreddit.parent / dname

            if not subreddit_dir.exists():
                subreddit_dir.mkdir()

            
            fname = f.stem
            fname = re.sub(r'\W+', '', fname)
            fname = fname + f.suffix
            fname = fname.lower()
            outpath = (output_dir / subreddit_dir/f"{fname}").with_suffix(".jpeg")

            im.save(outpath)
            im.close()
            pbar.set_description(f"writing: {outpath}")
            pbar.update(1)
            if(pbar.n == pbar.total) : break
        except Exception as e:
            pass

  0%|          | 0/8973 [00:00<?, ?it/s]

writing: /Users/reeteshmukul/me/data/reddit-tiny/apocalypse/scheduleddeliv_v9jc7m.jpeg: 100%|██████████| 8973/8973 [41:31<00:00,  3.60it/s]           
